In [1]:
!pip install biopython


[notice] A new release of pip is available: 23.3.1 -> 24.3.1
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
from collections import defaultdict, deque
from Bio import SeqIO
from concurrent.futures import ThreadPoolExecutor

def build_de_bruijn_graph(fastq_file, k):
    de_bruijn_graph = defaultdict(set)
    for record in SeqIO.parse(fastq_file, "fastq"):
        seq = str(record.seq)
        for i in range(len(seq) - k + 1):
            kmer = seq[i:i + k]
            if i < len(seq) - k:
                next_kmer = seq[i + 1:i + k + 1]
                de_bruijn_graph[kmer].add(next_kmer)
    return de_bruijn_graph

def traverse_graph(kmer, graph, visited):
    contig = kmer
    visited.add(kmer)
    
    while kmer in graph:
        next_kmers = list(graph[kmer] - visited)  # Only consider unvisited k-mers
        if not next_kmers:
            break
        kmer = next_kmers[0]
        visited.add(kmer)
        contig += kmer[-1]  # Add the last character of the next k-mer
    return contig

def build_contigs_parallel(graph):
    contigs = []
    visited = set()
    
    with ThreadPoolExecutor() as executor:
        futures = {
            executor.submit(traverse_graph, kmer, graph, visited): kmer
            for kmer in graph.keys() if kmer not in visited
        }
        for i, future in enumerate(futures, 1):
            contigs.append(future.result())
            print(f"Contig {i}: {future.result()}")
    
    return contigs

# Example usage
fastq_file = "16S_WT_day3_11_SRR2628505_1.fastq"  # Replace with your FASTQ file path
k = 21  # Length of k-mers
de_bruijn_graph = build_de_bruijn_graph(fastq_file, k)
contigs = build_contigs_parallel(de_bruijn_graph)

# Print contigs
for contig in contigs:
    print(contig)

Contig 1: CCTACGGGGGGCAGCAGTGAGGGATATTGGTCAATGGACGAGAGACTGAACCAGCCAAGTCGCGTGCAGGAAGACGGCCCTATGAGTTGTAAACTGCTTTTCCACAAGAGTAAGCTGGAGTACGCGTATTCGGCTGATCGTACTGTACGCATAAGGACCGGCTAACTCCGTGCCAGCCGCCGCCGTAATACGGAGGATCCCAGCGTTATCCGGGTTTATTGGGGTTAAAGGGTGAGTAGGGGGA
Contig 2: TACGGGGGGCAGCAGTGAGGAATAGTGGTCAATGGACGAGAGTCTGGACCAGCCAAGTAGCGTGAAGGGTGACTGCCCTATGGGTTGTAACTTCTTTTATATGGGAATAAAGCAGGGTATGCATACCCTCTTGGATGTACCATATGAATAAGGATTGGCTAACTCCGTGCCAGCAGCCGCGCGAAGACGGAGGGTGCGAGCGTTAGCCGGTTTTATTGGGTTTAAGGGTGGGTAGGGGGG
Contig 3: ACGGGGGGCAGCAGTGAGGAAGATTGGTCAATGGACGAGAGTCTAAACCAGCCAAGTAGCGTGAAG
Contig 4: GGGGGCAGCAGTGAGGAATATGGGTCAATGGACGAGAGTCTGATGCAGCCATGCCGCGTGTGTGAAGACGGCCTTCGGGATGGAAAGCACTTTCAGCGGGGAGGAAGGGAATAAAGTTAATACCTTTGCTCAATGACGTTACCCGCAGAAGAAGCAACGGCTAACTTCGTGACAGCAGCCGCGGTAATACGATGGGTGCAAGCGTTAATCGGAACTACTGGGCGTAAAGCGCACGCAGGCGGTTTGTTAAGTCAG
Contig 5: GGGGCAGCAGTGAGGAATATTGGGCAATGGACGAGAGTCTGAACCAGCCAAGGAGCGTGAAGGATGACTGCCCTAGGGGTTGTAAACTTCTTTTATAGGGGAGTAAAGCAGGGTATGCATACC
Contig 6: GGGCAGC

In [3]:
def remove_tips(de_bruijn_graph):
    tips = set()

    # Identify tips based on having a single outgoing edge
    for kmer, connections in de_bruijn_graph.items():
        if len(connections) == 1:
            next_kmer = list(connections)[0]
            if len(de_bruijn_graph.get(next_kmer, [])) > 1:  # Only consider if `next_kmer` is not itself a tip
                tips.add(kmer)
    
    # Remove identified tips from the graph
    for tip in tips:
        print("Tip:", tip)  # Printing identified tips for verification
        del de_bruijn_graph[tip]
        for kmer in de_bruijn_graph:
            de_bruijn_graph[kmer].discard(tip)  # Remove references to the tip

    return de_bruijn_graph

contigs = build_contigs_parallel(de_bruijn_graph)

# Remove tips from the De Bruijn graph
cleaned_graph = remove_tips(de_bruijn_graph)

print("--------------------------------------------------------")
# Optionally, you can rebuild contigs from the cleaned graph
cleaned_contigs = build_contigs_parallel(cleaned_graph)

# Print cleaned contigs
# for contig in cleaned_contigs:
#      print(contig)

Contig 1: CCTACGGGGGGCAGCAGTGAGGGATATTGGTCAATGGACGAGAGACTGAACCAGCCAAGTCGCGTGCAGGAAGACGGCCCTATGAGTTGTAAACTGCTTTTCCACAAGAGTAAGCTGGAGTACGCGTATTCGGCTGATCGTACTGTACGCATAAGGACCGGCTAACTCCGTGCCAGCCGCCGCCGTAATACGGAGGATCCCAGCGTTATCCGGGTTTATTGGGGTTAAAGGGTGAGTAGGGGGA
Contig 2: TACGGGGGGCAGCAGTGAGGAATAGTGGTCAATGGACGAGAGTCTGGACCAGCCAAGTAGCGTGAAGGGTGACTGCCCTATGGGTTGTAACTTCTTTTATATGGGAATAAAGCAGGGTATGCATACCCTCTTGGATGTACCATATGAATAAGGATTGGCTAACTCCGTGCCAGCAGCCGCGCGAAGACGGAGGGTGCGAGCGTTAGCCGGTTTTATTGGGTTTAAGGGTGGGTAGGGGGG
Contig 3: ACGGGGGGCAGCAGTGAGGAAGATTGGTCAATGGACGAGAGTCTAAACCAGCCAAGTAGCGTGAAG
Contig 4: GGGGGCAGCAGTGAGGAATATGGGTCAATGGACGAGAGTCTGATGCAGCCATGCCGCGTGTGTGAAGACGGCCTTCGGGATGGAAAGCACTTTCAGCGGGGAGGAAGGGAATAAAGTTAATACCTTTGCTCAATGACGTTACCCGCAGAAGAAGCAACGGCTAACTTCGTGACAGCAGCCGCGGTAATACGATGGGTGCAAGCGTTAATCGGAACTACTGGGCGTAAAGCGCACGCAGGCGGTTTGTTAAGTCAG
Contig 5: GGGGCAGCAGTGAGGAATATTGGGCAATGGACGAGAGTCTGAACCAGCCAAGGAGCGTGAAGGATGACTGCCCTAGGGGTTGTAAACTTCTTTTATAGGGGAGTAAAGCAGGGTATGCATACC
Contig 6: GGGCAGC

In [4]:
def remove_bubbles(graph):
    def find_bubble_paths(start_kmer, graph):
        # Breadth-First Search to find two paths from start_kmer that merge
        paths = []
        queue = deque([(start_kmer, [start_kmer])])
        visited = {start_kmer}
        
        while queue and len(paths) < 2:  # Only need two paths for a bubble
            current_kmer, path = queue.popleft()
            
            # End condition: we find a k-mer with multiple incoming edges (merging point)
            if len(graph[current_kmer]) > 1:
                paths.append(path)
                if len(paths) == 2:
                    return paths
            
            # Continue exploring outgoing edges
            for next_kmer in graph[current_kmer]:
                if next_kmer not in visited:
                    visited.add(next_kmer)
                    queue.append((next_kmer, path + [next_kmer]))
        
        return paths

    def widest_path(path1, path2):
        # Example width criteria: choose the longer path
        return path1 if len(path1) >= len(path2) else path2

    bubbles_removed = 0
    kmers_to_remove = set()
    
    for start_kmer in list(graph.keys()):
        # Find potential bubble paths
        paths = find_bubble_paths(start_kmer, graph)
        if len(paths) < 2:
            continue  # No bubble found
        
        # Resolve bubble by removing the narrower path
        wider_path = widest_path(paths[0], paths[1])
        narrower_path = paths[1] if wider_path == paths[0] else paths[0]
        
        # Mark kmers in the narrower path for removal
        for kmer in narrower_path:
            kmers_to_remove.add(kmer)
        
        bubbles_removed += 1

    # Remove k-mers in narrower paths from the graph
    for kmer in kmers_to_remove:
        if kmer in graph:
            del graph[kmer]
        for adj_kmer in graph:
            graph[adj_kmer].discard(kmer)
    
    print(f"Bubbles removed: {bubbles_removed}")
    return graph

# Example usage
cleaned_graph_with_bubbles_removed = remove_bubbles(cleaned_graph)

# Optionally, rebuild contigs from the cleaned and bubble-removed graph
cleaned_contigs_with_bubbles_removed = build_contigs_parallel(cleaned_graph_with_bubbles_removed)

Bubbles removed: 692
Contig 1: CTACGGGGGGCAGCAGTGAGGGATATTGGTCAAT
Contig 2: ATATTGGTCAATGGACGAGAGACTGAACCAGCCAA
Contig 3: TATTGGTCAATGGACGAGAGT
Contig 4: GACGAGAGTCTGAACCAGCCAGGTAGCGTGAAGGATGACTG
Contig 5: TGAACCAGCCAAGTAGCGTGAGG
Contig 6: GAACCAGCCAAGTAGCGTGAATGATGACTGCCCTATGG
Contig 7: CCAGCCAAGTAGCGTGAAGGAAG
Contig 8: GCGTGAAGGATGACTGCCCTAGGGGTTGTAAACTTCTTTTA
Contig 9: GGATGACTGCCCTATGGGTTGTGAACTTCTTTTATATGGGAATA
Contig 10: GATGACTGCCCTATGGGTTGT
Contig 11: TGCCCTATGGGTTGTAAACTTC
Contig 12: GCCCTATGGGTTGTAAACTTC
Contig 13: AAACTTCTTTTATATGGGAATCAAACAGGGTATGCATACCC
Contig 14: AAACAGGGTATGCATACCCTCCTGTGTGTACCATATGAATAA
Contig 15: AACAGGGTATGCATACCCTCTCGTATGTACCATATGCATAAG
Contig 16: AGGGTATGCATACCCTCTTGTTTGTACCATATGAATAAGGA
Contig 17: GGGTATGCATACCCTCTTGTAAGTACCATATGAATAAGGAT
Contig 18: TATGCATACCCTCTTGTATGTCCCATATGAATAAG
Contig 19: TACCCTCTTGTATGTACCATAGGAATAGGGATCGGCTAACTCCGTGC
Contig 20: CGAGCGTTATCCGGATTTATTGAGTTTAAAGGGTGCGTAGGC
Contig 21: GAGCGTTATCCGGATTTATTG
Contig 22: GTTTAAAGG